In this notebook, I will clean and preprocess the collected data and standardize it to be used in EDA and modeling. 

Table of contents:

# 1. Data Information

In this project, we collected heart rate data from 2 sources:
- https://github.com/rikluost/athlete_hr_predict (Riku Luostarinen) : This data is collected by the author using a smart watch and smart monitoring system over a period of 6 months (but not continuous). The data contains the following fields:

    * heart rate, beats per minute
    * enhanced_speed, meters per second
    * rolling_ave_alt, altitude change metres per second, 5-second moving average
    * cadence, steps per minute
    * distance, metres
    * enhanced_altitude, metres above the sea level

- https://github.com/INRIA/scikit-learn-mooc/blob/main/datasets/bike_rides.csv (INRIA) : This

# 2. Data Cleaning and preprocessing

## Packages

In [87]:
import os
import pandas as pd
import numpy as np

# Import plotly
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

## Short EDAs

To effectively clean the data, we will first perform some short EDAs to understand the data better. This will help us to identify the missing values, outliers, and other issues in the data. Doing this will also help us to understand the data better and make better decisions during the cleaning process.

### "Running" datasets

In [88]:
data_running = pd.DataFrame()
for file in os.listdir("./datasets/raw/running/fit_file_csv/"):
    data = pd.read_csv(f"./datasets/raw/running/fit_file_csv/{file}")
    data_running = pd.concat([data_running, data])

for file in os.listdir("./datasets/raw/running/fit_file_test_csv/"):
    data = pd.read_csv(f"./datasets/raw/running/fit_file_test_csv/{file}")
    data_running = pd.concat([data_running, data])
data_running.head()

timestamp  Unnamed: 0  lap  heart_rate  cadence  distance  \
0  2021-04-01 20:11:28+00:00         0.0  1.0        80.0     62.0      0.00   
1  2021-04-01 20:11:29+00:00         1.0  1.0        81.0     60.0      1.89   
2  2021-04-01 20:11:30+00:00         2.0  1.0        81.0     59.0      1.89   
3  2021-04-01 20:11:31+00:00         3.0  1.0        81.0     60.0      3.11   
4  2021-04-01 20:11:32+00:00         4.0  1.0        81.0    119.0      5.29   

   enhanced_altitude  enhanced_speed  calories  power  temperature  \
0               16.6           1.194       NaN    NaN         20.0   
1               16.6           1.390       NaN    NaN         20.0   
2               16.6           1.306       NaN    NaN         20.0   
3               16.6           1.306       NaN    NaN         20.0   
4               17.0           1.428       NaN    NaN         20.0   

   fractional_cadence  alt_difference  rolling_ave_alt  
0                 0.0             0.0             0.12  
1                 0.0             0.0             0.12  
2                 0.0             0.0             0.12  
3                 0.0             0.0             0.12  
4                 0.0             0.4             0.12

In [89]:
# Set time stamp as index
data_running.set_index("timestamp", inplace=True)
# Remove timezone from index
data_running.index = pd.to_datetime(data_running.index).tz_localize(None)

# Drop Unnamed: 0 column
data_running.drop("Unnamed: 0", axis=1, inplace=True)

data_running.head()

lap  heart_rate  cadence  distance  enhanced_altitude  \
timestamp                                                                    
2021-04-01 20:11:28  1.0        80.0     62.0      0.00               16.6   
2021-04-01 20:11:29  1.0        81.0     60.0      1.89               16.6   
2021-04-01 20:11:30  1.0        81.0     59.0      1.89               16.6   
2021-04-01 20:11:31  1.0        81.0     60.0      3.11               16.6   
2021-04-01 20:11:32  1.0        81.0    119.0      5.29               17.0   

                     enhanced_speed  calories  power  temperature  \
timestamp                                                           
2021-04-01 20:11:28           1.194       NaN    NaN         20.0   
2021-04-01 20:11:29           1.390       NaN    NaN         20.0   
2021-04-01 20:11:30           1.306       NaN    NaN         20.0   
2021-04-01 20:11:31           1.306       NaN    NaN         20.0   
2021-04-01 20:11:32           1.428       NaN    NaN         20.0   

                     fractional_cadence  alt_difference  rolling_ave_alt  
timestamp                                                                 
2021-04-01 20:11:28                 0.0             0.0             0.12  
2021-04-01 20:11:29                 0.0             0.0             0.12  
2021-04-01 20:11:30                 0.0             0.0             0.12  
2021-04-01 20:11:31                 0.0             0.0             0.12  
2021-04-01 20:11:32                 0.0             0.4             0.12

In [90]:
# Draw correlation matrix
corr = data_running.corr()
fig = px.imshow(corr)
fig.show()

In [91]:
# Data is in the format of "yyyy-mm-dd hh:mm:ss"
# Choose 1 day to plot
day = "2021-08-30"
mask = (data_running.index > day) & (data_running.index < day + " 23:59:59")
data_running_day = data_running.loc[mask]
data_running_day.head()

lap  heart_rate  cadence  distance  enhanced_altitude  \
timestamp                                                                    
2021-08-30 22:10:56  1.0        93.0      0.0      0.00              275.2   
2021-08-30 22:10:57  1.0        93.0      0.0      0.00              275.2   
2021-08-30 22:10:58  1.0        92.0      0.0      0.11              275.2   
2021-08-30 22:10:59  1.0        92.0      0.0      1.37              275.4   
2021-08-30 22:11:00  1.0        91.0      0.0      3.15              275.6   

                     enhanced_speed  calories  power  temperature  \
timestamp                                                           
2021-08-30 22:10:56             0.0      29.0   29.0         29.0   
2021-08-30 22:10:57             0.0      29.0   29.0         29.0   
2021-08-30 22:10:58             0.0      16.0   16.0         16.0   
2021-08-30 22:10:59             0.0      16.0   16.0         16.0   
2021-08-30 22:11:00             0.0      16.0   16.0         16.0   

                     fractional_cadence  alt_difference  rolling_ave_alt  
timestamp                                                                 
2021-08-30 22:10:56                 0.0             0.0             0.12  
2021-08-30 22:10:57                 0.0             0.0             0.12  
2021-08-30 22:10:58                 0.0             0.0             0.12  
2021-08-30 22:10:59                 0.0             0.2             0.12  
2021-08-30 22:11:00                 0.0             0.2             0.12

In [92]:
# Draw for all columns
columns = data_running_day.columns
# Each row will have 2 subplots
n_rows = int(np.ceil(len(columns)/2))
fig = make_subplots(rows=n_rows, cols=2, shared_xaxes=False, vertical_spacing=0.05, subplot_titles=columns)
for i, col_name in enumerate(data_running_day.columns):
    row = i//2 + 1
    col = i%2 + 1
    fig.add_trace(go.Scatter(x=data_running_day.index, y=data_running_day[col_name], mode='lines', name=col_name), row=row, col=col)
fig.update_layout(height=300*n_rows, title_text="Time series data of running variables", title_x=0.5)
fig.show()

In [93]:
tab = pd.DataFrame()

# Check for missing values
missing_values = data_running.isnull().sum()

# Create a table with missing values
tab = pd.concat([tab, missing_values], axis=1)
tab.columns = ["Missing values"]

# Check for outliers
# We will use the IQR method
Q1 = data_running.quantile(0.25)
Q3 = data_running.quantile(0.75)
IQR = Q3 - Q1
outliers = ((data_running < (Q1 - 1.5 * IQR)) | (data_running > (Q3 + 1.5 * IQR))).sum()

# Create a table with outliers
tab = pd.concat([tab, outliers], axis=1)
tab.columns = ["Missing values", "Outliers"]
tab

Missing values  Outliers
lap                              0      2929
heart_rate                       0      5343
cadence                          0     12636
distance                         0      3215
enhanced_altitude                0         0
enhanced_speed                   0     15575
calories                    121963         0
power                       121963         0
temperature                      0      2485
fractional_cadence               0         0
alt_difference                   0     73561
rolling_ave_alt                  0      5543

### "Biking" datasets

In [94]:
data_biking = pd.read_csv("./datasets/raw/biking/bike_rides.csv")
data_biking.head()

timestamp  power  heart-rate  cadence  speed  acceleration  \
0  2020-08-18 14:43:19  150.0       102.0     64.0  4.325        0.0880   
1  2020-08-18 14:43:20  161.0       103.0     64.0  4.336        0.0842   
2  2020-08-18 14:43:21  163.0       105.0     66.0  4.409        0.0234   
3  2020-08-18 14:43:22  156.0       106.0     66.0  4.445        0.0016   
4  2020-08-18 14:43:23  148.0       106.0     67.0  4.441        0.1144   

      slope  
0 -0.033870  
1 -0.033571  
2 -0.033223  
3 -0.032908  
4  0.000000

In [95]:
# Set time stamp as index
data_biking.set_index("timestamp", inplace=True)
data_biking.head()

power  heart-rate  cadence  speed  acceleration     slope
timestamp                                                                     
2020-08-18 14:43:19  150.0       102.0     64.0  4.325        0.0880 -0.033870
2020-08-18 14:43:20  161.0       103.0     64.0  4.336        0.0842 -0.033571
2020-08-18 14:43:21  163.0       105.0     66.0  4.409        0.0234 -0.033223
2020-08-18 14:43:22  156.0       106.0     66.0  4.445        0.0016 -0.032908
2020-08-18 14:43:23  148.0       106.0     67.0  4.441        0.1144  0.000000

In [96]:
# Draw correlation matrix
corr = data_biking.corr()
fig = px.imshow(corr)
fig.show()

In [97]:
# Data is in the format of "yyyy-mm-dd hh:mm:ss"
# Choose 1 day to plot
day = "2020-08-18"
mask = (data_biking.index > day) & (data_biking.index < day + " 23:59:59")
data_biking_day = data_biking.loc[mask]
data_biking_day.head()

power  heart-rate  cadence  speed  acceleration     slope
timestamp                                                                     
2020-08-18 14:43:19  150.0       102.0     64.0  4.325        0.0880 -0.033870
2020-08-18 14:43:20  161.0       103.0     64.0  4.336        0.0842 -0.033571
2020-08-18 14:43:21  163.0       105.0     66.0  4.409        0.0234 -0.033223
2020-08-18 14:43:22  156.0       106.0     66.0  4.445        0.0016 -0.032908
2020-08-18 14:43:23  148.0       106.0     67.0  4.441        0.1144  0.000000

In [98]:
# Draw for all columns
columns = data_biking_day.columns
# Each row will have 2 subplots
n_rows = int(np.ceil(len(columns)/2))
fig = make_subplots(rows=n_rows, cols=2, shared_xaxes=False, vertical_spacing=0.1, subplot_titles=columns)
for i, col_name in enumerate(data_biking_day.columns):
    row = i//2 + 1
    col = i%2 + 1
    fig.add_trace(go.Scatter(x=data_biking_day.index, y=data_biking_day[col_name], mode='lines', name=col_name), row=row, col=col)
fig.update_layout(height=300*n_rows, title_text="Time series data of biking variables", title_x=0.5)
fig.show()

In [99]:
tab = pd.DataFrame()

# Check for missing values
missing_values = data_biking.isnull().sum()

# Create a table with missing values
tab = pd.concat([tab, missing_values], axis=1)
tab.columns = ["Missing values"]

# Check for outliers
# We will use the IQR method
Q1 = data_biking_day.quantile(0.25)
Q3 = data_biking_day.quantile(0.75)
IQR = Q3 - Q1
outliers = ((data_biking < (Q1 - 1.5 * IQR)) | (data_biking > (Q3 + 1.5 * IQR))).sum()

# Create a table with outliers
tab = pd.concat([tab, outliers], axis=1)
tab.columns = ["Missing values", "Outliers"]
tab

Missing values  Outliers
power                      0      1513
heart-rate                 0      1045
cadence                    0      4897
speed                      0       911
acceleration               0      3948
slope                      0     17341

## Choosing the right data for both datasets

Before cleaning and preprocessing the data, we need to decide which columns we will use in our analysis. This is important because we don't want to waste time cleaning and preprocessing data that we won't use in our analysis.

Based on the short EDAs, we have identified a feel crucial columns that we will use in our analysis. These columns are:

- heart_rate
- enhanced_speed/speed
- cadence

There are few reasons why we chose these columns:
1. These columns are both available in both datasets. This will help us to merge the datasets easily.
2. These columns have the least missing values. This will help us to avoid imputing missing values.
3. These columns are crucial for our analysis. For example, heart rate, speed, and power are important metrics for measuring the performance of an athlete. Cadence is also important for measuring the efficiency of an athlete.
4. Most monitoring systems collect these metrics. For example, most smart watches collect heart rate and speed data. Some fitness trackers also collect power and cadence data.

In [100]:
features = ["heart-rate", "speed", "cadence"]
data_running.rename(columns={"enhanced_speed": "speed", "heart_rate" : "heart-rate"}, inplace=True)
data_running = data_running[features]
data_biking = data_biking[features]

## Cleaning

Based on the info above, I will clean the data as follows:

1. Remove the rows with missing values
2. Remove duplicates
3. Cap rows with outliers


1. Remove the rows with missing values

In [101]:
# Remove missing values from running data
data_running = data_running.dropna()

# Remove missing values from biking data
data_biking = data_biking.dropna()

2. Remove duplicates

In [102]:
# Remove duplicates
data_running = data_running.drop_duplicates()
data_biking = data_biking.drop_duplicates()

3. Cap rows with outliers

In [103]:
# Cap outliers so that they are within 1.5 * IQR
Q1 = data_running.quantile(0.25)

Q3 = data_running.quantile(0.75)
IQR = Q3 - Q1
data_running = data_running.clip(Q1 - 1.5*IQR, Q3 + 1.5*IQR, axis=1)

In [104]:
# Cap outliers so that they are within 1.5 * IQR
Q1 = data_biking.quantile(0.25)
Q3 = data_biking.quantile(0.75)
IQR = Q3 - Q1
data_biking = data_biking.clip(Q1 - 1.5*IQR, Q3 + 1.5*IQR, axis=1)

In [105]:
data_running.to_csv("./datasets/cleaned/running.csv")

In [106]:
data_biking.to_csv("./datasets/cleaned/biking.csv")